<a href="https://colab.research.google.com/github/tuonganhdo/kickstarter-analysis/blob/main/Kickstarter_Analysis_Project.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Setting up

In [ ]:
!pip install pyspark pandas matplotlib seaborn

In [ ]:
# imports
from pyspark.sql import SparkSession
from pyspark.sql.functions import isnan, when, count, col, to_date, when, year
import plotly.express as px
import plotly.graph_objects as go
from pyspark.ml.feature import StringIndexer, OneHotEncoder, VectorAssembler
from pyspark.ml.classification import RandomForestClassifier
from pyspark.ml.evaluation import MulticlassClassificationEvaluator

In [ ]:
# create session
spark = SparkSession.builder \
    .appName("Kickstarter Project Analysis") \
    .getOrCreate()

In [ ]:
# check initialization
spark.sql('''select 'spark' as hello''').show()

+-----+
|hello|
+-----+
|spark|
+-----+



# Data cleaning & transformation

In [ ]:
# load dataset
kickstarter_raw = spark.read.csv("kickstarter_projects.csv", header=True, inferSchema=True)
kickstarter_data_dict = spark.read.csv("kickstarter_projects_data_dictionary.csv", header=True, inferSchema=True)

In [ ]:
# show data dictionary
kickstarter_data_dict.show(truncate=False)

+-----------+---------------------------------------------------------------+
|Field      |Description                                                    |
+-----------+---------------------------------------------------------------+
|ID         |Internal kickstarter id                                        |
|Name       |Name of the project                                            |
|Category   |Project category                                               |
|Subcategory|Project subcategory                                            |
|Country    |Country the project is from                                    |
|Launched   |Date the project was launched                                  |
|Deadline   |Deadline date for crowdfunding                                 |
|Goal       |Amount of money the creator needs to complete the project (USD)|
|Pledged    |Amount of money pledged by the crowd (USD)                     |
|Backers    |Number of backers                                  

In [ ]:
# schema
kickstarter_raw.printSchema()

root
 |-- ID: integer (nullable = true)
 |-- Name: string (nullable = true)
 |-- Category: string (nullable = true)
 |-- Subcategory: string (nullable = true)
 |-- Country: string (nullable = true)
 |-- Launched: string (nullable = true)
 |-- Deadline: string (nullable = true)
 |-- Goal: string (nullable = true)
 |-- Pledged: string (nullable = true)
 |-- Backers: string (nullable = true)
 |-- State: string (nullable = true)



Right from the schema we can see that data conversions will need to be done/ Backers, Pledged, and Goal should all be numeric fields, and Launched and Date should be date/timestamps.

In [ ]:
# quick look at the data
kickstarter_raw.show(5)

+----------+--------------------+------------+------------+-------------+-------------------+----------+-----+-------+-------+----------+
|        ID|                Name|    Category| Subcategory|      Country|           Launched|  Deadline| Goal|Pledged|Backers|     State|
+----------+--------------------+------------+------------+-------------+-------------------+----------+-----+-------+-------+----------+
|1860890148|Grace Jones Does ...|     Fashion|     Fashion|United States|2009-04-21 21:02:48|2009-05-31| 1000|    625|     30|    Failed|
| 709707365|CRYSTAL ANTLERS U...|Film & Video|      Shorts|United States|2009-04-23 00:07:53|2009-07-20|80000|     22|      3|    Failed|
|1703704063| drawing for dollars|         Art|Illustration|United States|2009-04-24 21:52:03|2009-05-03|   20|     35|      3|Successful|
|    727286|Offline Wikipedia...|  Technology|    Software|United States|2009-04-25 17:36:21|2009-07-14|   99|    145|     25|Successful|
|1622952265|          Pantshirts| 

In [ ]:
# overview
kickstarter_raw.describe().show()

+-------+--------------------+--------------------+--------------------+--------------------+---------------+--------------------+----------+------------------+-----------------+------------------+-----------------+
|summary|                  ID|                Name|            Category|         Subcategory|        Country|            Launched|  Deadline|              Goal|          Pledged|           Backers|            State|
+-------+--------------------+--------------------+--------------------+--------------------+---------------+--------------------+----------+------------------+-----------------+------------------+-----------------+
|  count|              374853|              374853|              374853|              374850|         374849|              374848|    374848|            374848|           374848|            374848|           374848|
|   mean|1.0746564482396193E9|            Infinity|                 4.0|              1005.0|           NULL|                NULL|      

Here we see that
- Category, subcategory, and state contain numeric values even though they are text fields
- Country seems to contain non-country values
- Launched and Deadline both contain non-date values
- Some projects have a goal of 0, which won't be very conductive to our analysis

And so we clean!

In [ ]:
og_data_size = kickstarter_raw.count()
print(f"Original data size: {og_data_size}")

Original data size: 374853


## Null values

In [ ]:
# check for null values
kickstarter_raw.select([count(when(isnan(c), c)).alias(c) for c in kickstarter_raw.columns]).show()

+---+----+--------+-----------+-------+--------+--------+----+-------+-------+-----+
| ID|Name|Category|Subcategory|Country|Launched|Deadline|Goal|Pledged|Backers|State|
+---+----+--------+-----------+-------+--------+--------+----+-------+-------+-----+
|  0|   0|       0|          0|      0|       0|       0|   0|      0|      0|    0|
+---+----+--------+-----------+-------+--------+--------+----+-------+-------+-----+



## Casting launched and deadline to date

In [ ]:
# convert date columns
kickstarter = kickstarter_raw.withColumn("Launched", to_date(col("Launched")))
kickstarter = kickstarter.withColumn("Deadline", to_date(col("Deadline")))

kickstarter.printSchema()

root
 |-- ID: integer (nullable = true)
 |-- Name: string (nullable = true)
 |-- Category: string (nullable = true)
 |-- Subcategory: string (nullable = true)
 |-- Country: string (nullable = true)
 |-- Launched: date (nullable = true)
 |-- Deadline: date (nullable = true)
 |-- Goal: string (nullable = true)
 |-- Pledged: string (nullable = true)
 |-- Backers: string (nullable = true)
 |-- State: string (nullable = true)



In [ ]:
# remove non-date values
kickstarter = kickstarter.where(col("Launched").isNotNull())
kickstarter = kickstarter.where(col("Deadline").isNotNull())

In [ ]:
# number of rows removed & portion of data remaining
num_rows_removed = og_data_size - kickstarter.count()
print(f"Number of rows removed: {num_rows_removed}")
print(f"Portion of data remaining: {kickstarter.count() / og_data_size}")

Number of rows removed: 1290
Portion of data remaining: 0.9965586509911886


## Goal, pledged, and backers

### Casting to numeric data types

In [ ]:
# check that goal, pledged, backers are all numeric
kickstarter.select("ID", kickstarter.Goal.cast("float").isNull().alias("isNull")).where(col("isNull") == True).show()
kickstarter.select("ID", kickstarter.Pledged.cast("float").isNull().alias("isNull")).where(col("isNull") == True).show()
kickstarter.select("ID", kickstarter.Backers.cast("float").isNull().alias("isNull")).where(col("isNull") == True).show()

+---+------+
| ID|isNull|
+---+------+
+---+------+

+---+------+
| ID|isNull|
+---+------+
+---+------+

+---+------+
| ID|isNull|
+---+------+
+---+------+



In [ ]:
# convert to numeric columns
kickstarter = kickstarter.withColumn("Goal", kickstarter.Goal.cast("float"))
kickstarter = kickstarter.withColumn("Pledged", kickstarter.Pledged.cast("float"))
kickstarter = kickstarter.withColumn("Backers", kickstarter.Backers.cast("int"))

In [ ]:
kickstarter.printSchema()

root
 |-- ID: integer (nullable = true)
 |-- Name: string (nullable = true)
 |-- Category: string (nullable = true)
 |-- Subcategory: string (nullable = true)
 |-- Country: string (nullable = true)
 |-- Launched: date (nullable = true)
 |-- Deadline: date (nullable = true)
 |-- Goal: float (nullable = true)
 |-- Pledged: float (nullable = true)
 |-- Backers: integer (nullable = true)
 |-- State: string (nullable = true)
 |-- State_Indexed: double (nullable = false)
 |-- State_OneHot: vector (nullable = true)



In [ ]:
# number of goal outliers
goal_quartiles = kickstarter.approxQuantile("Goal", [0.25, 0.5, 0.75], 0.0)
goal_iqr = goal_quartiles[2] - goal_quartiles[0]
num_outliers = kickstarter.where((col("Goal") > goal_quartiles[2] + 1.5 * goal_iqr) | (col("Goal") < goal_quartiles[0] - 1.5 * goal_iqr)).count()

### Dropping non-numeric values

In [ ]:
kickstarter = kickstarter.where(col("Goal").isNotNull())
kickstarter = kickstarter.where(col("Pledged").isNotNull())
kickstarter = kickstarter.where(col("Backers").isNotNull())

### Dropping goal outliers

In [ ]:
fig = px.box(kickstarter.toPandas(), y="Goal")
fig

In [ ]:
# find iqr and quartiles
goal_quartiles = kickstarter.approxQuantile("Goal", [0.25, 0.5, 0.75], 0.0)
goal_iqr = goal_quartiles[2] - goal_quartiles[0]

In [ ]:
# drop goal outliers
kickstarter = kickstarter.where((col("Goal") <= goal_quartiles[2] + 1.5 * goal_iqr) & (col("Goal") >= goal_quartiles[0] - 1.5 * goal_iqr))

In [ ]:
# number of rows after cleaning
print(f"Number of rows after cleaning: {kickstarter.count()}")
print(f"Portion of data remaining: {kickstarter.count()/og_data_size}")

Number of rows after cleaning: 328959
Portion of data remaining: 0.8775680066586101


## Post-cleaning summary

# Visualization

### Rate of success

In [ ]:
kickstarter.select(["State", "State_Indexed"]).groupBy("State").max().show()

+----------+------------------+
|     State|max(State_Indexed)|
+----------+------------------+
| Suspended|               4.0|
|  Canceled|               2.0|
|    Failed|               0.0|
|Successful|               1.0|
|      Live|               3.0|
+----------+------------------+



In [ ]:
num_successful = kickstarter.where(col("State_Indexed") == 1).count()
print(f"Number of successful projects: {num_sucessful}")

pct_successful = num_sucessful / kickstarter.count() * 100
print(f"Percentage of successful projects: {pct_successful:.2f}%")

Number of successful projects: 127402
Percentage of successful projects: 38.73%


### Success rate by category

In [ ]:
kickstarter_succeeded = kickstarter.withColumn("Success", when(col("State_Indexed") == 1, 1).otherwise(0))
success_rate_by_category = kickstarter_succeeded.groupBy("Category").agg({"Success": "mean", "ID": "count"}).withColumnRenamed("avg(Success)", "Success_Rate").withColumnRenamed("count(ID)", "Project_Count")

In [ ]:
fig = px.bar(success_rate_by_category.sort("Success_Rate", ascending=False).toPandas(), x="Category", y="Success_Rate", color="Project_Count", title="Success Rate by Category")
fig

The success rate looks to be higher for projects in the arts, but these are also the categories with the smallest numbers of projects, which might be skewing the results. As the success rate decreases, we see the project count go up and then back down.

### Project success rates over the years

In [ ]:
# add a column with the year of each project
kickstarter_years = kickstarter_succeeded.withColumn("Year", year(col("Launched")))

# remove 2018 projects since they haven't concluded
kickstarter_years = kickstarter_years.where(col("Year") < 2018)

# group by year and column
kickstarter_years_categories = kickstarter_years.groupBy(["Year","Category"]).agg({"Success": "mean", "ID": "count"}).withColumnRenamed("avg(Success)", "Success_Rate").withColumnRenamed("count(ID)", "Project_Count").sort("Year")

# plot
fig = px.line(kickstarter_years_categories.toPandas(), x="Year", y="Success_Rate", color="Category", title="Project Success Rates Over the Years")
fig

### Projects with the greatest goal completion

In [ ]:
goal_completion = kickstarter.withColumn("Goal_Completion", col("Pledged") / col("Goal"))
top_goal_completion = goal_completion.sort("Goal_Completion", ascending=False).select("ID", "Name", "Goal", "Pledged", "Goal_Completion").limit(1000).show(truncate=False)

+----------+--------------------------------------------------------------+----+--------+---------------+
|ID        |Name                                                          |Goal|Pledged |Goal_Completion|
+----------+--------------------------------------------------------------+----+--------+---------------+
|9509582   |VULFPECK /// The Beautiful Game                               |1.0 |104278.0|104278.0       |
|1947298033|Re-covering with Friends                                      |1.0 |68764.0 |68764.0        |
|907870443 |VULFPECK /// Thrill of the Arts                               |1.0 |55267.0 |55267.0        |
|1388400809|Energy Hook                                                   |1.0 |41535.0 |41535.0        |
|1413857335|Band of Brothers 2nd Chance                                   |1.0 |32843.0 |32843.0        |
|521903377 |CLOCKWRIGHT: Large-Scale Analogue Time Machines               |1.0 |27588.0 |27588.0        |
|951161619 |Heartbreak Hits – Theo Katzman's S

In [ ]:
fig = px.histogram(goal_completion.toPandas(), x="Goal", title="Distribution of Goal Completion")
fig

# Model

In [ ]:
# imports
from pyspark.ml.feature import VectorAssembler

In [ ]:
kickstarter.printSchema()

root
 |-- ID: integer (nullable = true)
 |-- Name: string (nullable = true)
 |-- Category: string (nullable = true)
 |-- Subcategory: string (nullable = true)
 |-- Country: string (nullable = true)
 |-- Launched: date (nullable = true)
 |-- Deadline: date (nullable = true)
 |-- Goal: float (nullable = true)
 |-- Pledged: float (nullable = true)
 |-- Backers: integer (nullable = true)
 |-- State: string (nullable = true)
 |-- State_Indexed: double (nullable = false)
 |-- State_OneHot: vector (nullable = true)



In [ ]:
categorical = ['Category', 'Subcategory', 'Country', 'State']

## Preparing dataset

In [ ]:
# initialize StringIndexer model and transform our data
indexer = StringIndexer(inputCol="State", outputCol="State_Indexed")
kickstarter = indexer.fit(kickstarter).transform(kickstarter)

kickstarter.show(5, truncate=False)

+----------+-----------------------------------------------------------+------------+------------+-------------+----------+----------+-----+-------+-------+----------+-------------+
|ID        |Name                                                       |Category    |Subcategory |Country      |Launched  |Deadline  |Goal |Pledged|Backers|State     |State_Indexed|
+----------+-----------------------------------------------------------+------------+------------+-------------+----------+----------+-----+-------+-------+----------+-------------+
|1860890148|Grace Jones Does Not Give A F$#% T-Shirt (limited Edition) |Fashion     |Fashion     |United States|2009-04-21|2009-05-31|1000 |625    |30     |Failed    |0.0          |
|709707365 |CRYSTAL ANTLERS UNTITLED MOVIE                             |Film & Video|Shorts      |United States|2009-04-23|2009-07-20|80000|22     |3      |Failed    |0.0          |
|1703704063|drawing for dollars                                        |Art         |Illus

In [ ]:
# one-hot encoding
encoder = OneHotEncoder(inputCol="State_Indexed", outputCol="State_OneHot")
kickstarter = encoder.fit(kickstarter).transform(kickstarter)
kickstarter.show(5, truncate=False)

+----------+-----------------------------------------------------------+------------+------------+-------------+----------+----------+-----+-------+-------+----------+-------------+-------------+
|ID        |Name                                                       |Category    |Subcategory |Country      |Launched  |Deadline  |Goal |Pledged|Backers|State     |State_Indexed|State_OneHot |
+----------+-----------------------------------------------------------+------------+------------+-------------+----------+----------+-----+-------+-------+----------+-------------+-------------+
|1860890148|Grace Jones Does Not Give A F$#% T-Shirt (limited Edition) |Fashion     |Fashion     |United States|2009-04-21|2009-05-31|1000 |625    |30     |Failed    |0.0          |(4,[0],[1.0])|
|709707365 |CRYSTAL ANTLERS UNTITLED MOVIE                             |Film & Video|Shorts      |United States|2009-04-23|2009-07-20|80000|22     |3      |Failed    |0.0          |(4,[0],[1.0])|
|1703704063|drawing 